In [1]:
%load_ext autoreload
%autoreload 2

import sys
from collections import OrderedDict

import matplotlib.pyplot as plt
import numpy as np
import pandas as pd

sys.path.append("../../..")

import lib.ehr.example_datasets.mimiciv_aki as m4aki
from lib.ehr.tvx_ehr import TVxEHR
from lib.utils import modified_environ, write_config


In [2]:
# create a database connection
sqluser = 'postgres'
dbname = 'mimiciv'
hostname = 'localhost'
password = 'qwerasdf'
port = '5432'

url = f'postgresql+psycopg2://{sqluser}:{password}@{hostname}:{port}/{dbname}'

with modified_environ(MIMICIV_URL=url):
    mimiciv_config = m4aki.AKIMIMICIVDatasetConfig()
    tvx_config = m4aki.TVxAKIMIMICIVDatasetConfig()

    write_config(mimiciv_config.to_dict(), 'dataset_mimiciv_aki_config.json')
    write_config(tvx_config.to_dict(), 'tvx_mimiciv_aki_config.json')


In [7]:
with modified_environ(MIMICIV_URL=url):
    dataset = m4aki.AKIMIMICIVDataset(config=mimiciv_config)           

Exception ignored in: <function _xla_gc_callback at 0x730ac989fba0>
Traceback (most recent call last):
  File "/home/asem/GP/env/icenode-dev/lib/python3.11/site-packages/jax/_src/lib/__init__.py", line 98, in _xla_gc_callback
    def _xla_gc_callback(*args):
    
KeyboardInterrupt: 


KeyboardInterrupt: 

In [4]:
dataset = dataset.execute_pipeline()

Transforming Dataset:   0%|          | 0/10 [00:00<?, ?transformations/s]

In [5]:
tvx = m4aki.TVxAKIMIMICIVDataset(config=tvx_config, dataset=dataset)

In [6]:
tvx = tvx.execute_pipeline()

Transforming Dataset:   0%|          | 0/10 [00:00<?, ?transformations/s]

/home/asem/GP/ICENODE/notebooks/mimic_icu/exploratory/../../../lib/ehr/tvx_transformations.py:712: FutureWarning: A grouping was used that is not in the columns of the DataFrame and so was excluded from the result. This grouping will be included in a future version of pandas. Add the grouping as a column of the DataFrame to silence this warning.
  return g.apply(val_mask).groupby(0).apply(gen_observation)
/home/asem/GP/ICENODE/notebooks/mimic_icu/exploratory/../../../lib/ehr/tvx_transformations.py:712: FutureWarning: A grouping was used that is not in the columns of the DataFrame and so was excluded from the result. This grouping will be included in a future version of pandas. Add the grouping as a column of the DataFrame to silence this warning.
  return g.apply(val_mask).groupby(0).apply(gen_observation)
/home/asem/GP/ICENODE/notebooks/mimic_icu/exploratory/../../../lib/ehr/tvx_transformations.py:712: FutureWarning: A grouping was used that is not in the columns of the DataFrame and 

In [15]:
print('x')

x


In [7]:
tvx.subjects['10000032']

SegmentedPatient(
  subject_id='10000032',
  static_info=StaticInfo(
    gender=CodesVector(vec=bool[2](numpy), scheme='mimiciv.aki_study.gender'),
    ethnicity=CodesVector(
      vec=bool[5](numpy),
      scheme='mimiciv.aki_study.target_ethnicity'
    ),
    date_of_birth=Timestamp('2128-01-01 00:00:00')
  ),
  admissions=[
    SegmentedAdmission(
      admission_id='22595853',
      admission_dates=AdmissionDates(
        admission=Timestamp('2180-05-06 22:23:00'),
        discharge=Timestamp('2180-05-07 17:15:00')
      ),
      dx_codes=CodesVector(vec=bool[17375](numpy), scheme='dx_icd9'),
      dx_codes_history=CodesVector(vec=bool[17375](numpy), scheme='dx_icd9'),
      outcome=CodesVector(vec=bool[11535](numpy), scheme='dx_icd9_v1'),
      observables=SegmentedInpatientObservables(
        time=f64[1](numpy),
        value=f16[1,100](numpy),
        mask=bool[1,100](numpy),
        extra_layers=(),
        indexed_split=i64[2](numpy)
      ),
      interventions=SegmentedInpa

In [8]:
tvx.subjects['10000032'].admissions[2].interventions.icu_inputs

array([[0.     , 0.     , 0.     , ..., 0.     , 0.     , 0.     ],
       [0.06665, 0.     , 0.     , ..., 0.     , 0.     , 0.     ],
       [0.06665, 0.     , 0.     , ..., 0.     , 0.     , 0.     ],
       ...,
       [0.     , 0.     , 0.     , ..., 0.     , 0.     , 0.     ],
       [0.     , 0.     , 0.     , ..., 0.     , 0.     , 0.     ],
       [0.     , 0.     , 0.     , ..., 0.     , 0.     , 0.     ]],
      dtype=float16)

In [9]:
tvx.dataset.pipeline_report.to_csv('dataset_pipeline_report.csv')

In [10]:
tvx.pipeline_report.to_csv('tvx_pipeline_report.csv')

In [ ]:
tvx.save('tvx_aki.h5', True)

In [4]:
tvx = m4aki.TVxAKIMIMICIVDataset.load('tvx_aki.h5')

In [12]:
from lib.ehr.tvx_transformations import TrainingSplitGroups
tvx_list = TrainingSplitGroups()(tvx, n_groups=10, seed=0)

In [13]:
len(tvx_list)

10

In [ ]:
for i, tvx_item in enumerate(tvx_list):
    tvx_item.save(f'tvx_aki_training_groups/tvx_aki_{i}.h5', True)

/home/asem/GP/env/icenode-dev/lib/python3.11/site-packages/tables/path.py:137: NaturalNameWarning: object name is not a valid Python identifier: '0'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*$``; you will not be able to use natural naming to access this object; using ``getattr()`` will still work, though
  check_attribute_name(name)
/home/asem/GP/env/icenode-dev/lib/python3.11/site-packages/tables/path.py:137: NaturalNameWarning: object name is not a valid Python identifier: '0'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*$``; you will not be able to use natural naming to access this object; using ``getattr()`` will still work, though
  check_attribute_name(name)
/home/asem/GP/env/icenode-dev/lib/python3.11/site-packages/tables/path.py:137: NaturalNameWarning: object name is not a valid Python identifier: '1'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*$``; you will not be able to use natural naming to access this object; using ``getattr()`` will s

In [17]:
print('x')

x


In [5]:
tvx0 = m4aki.TVxAKIMIMICIVDataset.load('tvx_aki_training_groups/tvx_aki_0.h5')

In [6]:
len(tvx0.subjects)

3006

In [12]:
from lib.ml.embeddings import InICENODEEmbeddingsConfig, InterventionsEmbeddingsConfig
from lib.ml.in_models import InpatientModelConfig, InICENODE

In [13]:
emb_config = InICENODEEmbeddingsConfig(dx_codes=50, demographic=10, 
                                       interventions=InterventionsEmbeddingsConfig(icu_inputs=10,
                                                                                   icu_procedures=10,
                                                                                   hosp_procedures=10,
                                                                                   interventions=20))

model_config = InpatientModelConfig(state=50, lead_predictor='monotonic')

In [15]:
import jax.random as jrandom

model = InICENODE(config=model_config, embeddings_config=emb_config,
                  lead_times=(12., 24., 48.),
                  dx_codes_size=len(tvx0.scheme.dx_discharge),
                  outcome_size=None,
                  icu_inputs_grouping=tvx0.icu_inputs_grouping,
                  icu_procedures_size=len(tvx0.scheme.icu_procedures),
                  hosp_procedures_size=len(tvx0.scheme.hosp_procedures),
                  demographic_size=tvx0.demographic_vector_size,
                  observables_size=len(tvx0.scheme.obs),
                  key=jrandom.PRNGKey(0))
                  

In [16]:
model

InICENODE(
  config=InpatientModelConfig(
    embedding=Config(),
    state=50,
    lead_predictor='monotonic'
  ),
  regularisation=None,
  f_emb=AdmissionEmbedding(
    config=AdmissionGenericEmbeddingsConfig(
      dx_codes=50,
      interventions=InterventionsEmbeddingsConfig(
        icu_inputs=10,
        icu_procedures=10,
        hosp_procedures=10,
        interventions=20
      ),
      demographic=10,
      observables=None
    ),
    f_dx_codes_emb=MLP(
      layers=(
        Linear(
          weight=f32[100,17375],
          bias=f32[100],
          in_features=17375,
          out_features=100,
          use_bias=True
        ),
        Linear(
          weight=f32[50,100],
          bias=f32[50],
          in_features=100,
          out_features=50,
          use_bias=True
        )
      ),
      activation=<wrapped function relu>,
      final_activation=<wrapped function tanh>,
      use_bias=True,
      use_final_bias=True,
      in_size=17375,
      out_size=50,
    